In [3]:
"""
DeepFake Detection Script for Dataset Evaluation
This script processes images in real/fake folders and evaluates model performance.
"""

import os
import io
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from PIL import Image as PILImage
from tensorflow.keras.models import load_model
from tensorflow.keras.applications.xception import preprocess_input
from sklearn.metrics import confusion_matrix, classification_report, roc_curve, auc
import logging
import time
from tqdm import tqdm

# Set up logging
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(name)s - %(levelname)s - %(message)s',
    handlers=[
        logging.FileHandler("deepfake_detection.log"),
        logging.StreamHandler()
    ]
)
logger = logging.getLogger("DeepFakeDetector")

# Global variable for model
deepfake_model = None

def load_model_once(model_path):
    """
    Load the pre-trained deepfake detection model once and store in global variable.
    
    Args:
        model_path: Path to the saved model
        
    Returns:
        Loaded model or None if loading fails
    """
    global deepfake_model
    
    if deepfake_model is not None:
        return deepfake_model
        
    try:
        logger.info(f"Loading model from {model_path}")
        deepfake_model = load_model(model_path)
        logger.info("Model loaded successfully")
        return deepfake_model
    except Exception as e:
        logger.error(f"Failed to load model: {str(e)}")
        return None

def preprocess_image(img_path):
    """
    Preprocess image for model input.
    
    Args:
        img_path: Path to the image file
        
    Returns:
        Preprocessed image array ready for model input
    """
    try:
        img = PILImage.open(img_path)
        img = img.resize((299, 299))  # Xception input size
        img = img.convert('RGB')
        
        # Convert to numpy array and normalize
        img_array = np.array(img)
        img_array = img_array.astype('float32') / 255.0
        img_array = np.expand_dims(img_array, axis=0)
        
        return img_array
    except Exception as e:
        logger.error(f"Error preprocessing image {img_path}: {str(e)}")
        return None

def detect_deepfake(img_path, model):
    """
    Perform deepfake detection on an image.
    
    Args:
        img_path: Path to the image file
        model: Loaded model
        
    Returns:
        dict: Detection results including label and confidence
    """
    # Preprocess image for the model
    img_array = preprocess_image(img_path)
    
    if img_array is None:
        return {"label": "Unknown", "confidence": 0.0}
    
    try:
        # Make prediction
        prediction = model.predict(img_array)[0][0]
        
        # Interpret prediction
        label = "Fake" if prediction > 0.5 else "Real"
        confidence = float(prediction) if label == "Fake" else 1.0 - float(prediction)
        
        return {
            "label": label,
            "confidence": confidence
        }
    except Exception as e:
        logger.error(f"Error in deepfake detection: {str(e)}")
        return {"label": "Unknown", "confidence": 0.0}

def evaluate_model(base_dir, model_path, output_dir="results"):
    """
    Evaluate model on test directories with real and fake images.
    
    Args:
        base_dir: Base directory containing 'real' and 'fake' subdirectories
        model_path: Path to the model file
        output_dir: Directory to save results
    """
    # Load model
    model = load_model_once(model_path)
    if model is None:
        logger.error("Failed to load model. Exiting.")
        return
    
    results = []
    
    # Process real images
    real_dir = os.path.join(base_dir, "real")
    if os.path.isdir(real_dir):
        logger.info(f"Processing real images from {real_dir}")
        real_images = [f for f in os.listdir(real_dir) 
                      if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
        
        for img_file in tqdm(real_images, desc="Processing Real Images"):
            img_path = os.path.join(real_dir, img_file)
            detection = detect_deepfake(img_path, model)
            
            results.append({
                "filename": img_file,
                "path": img_path,
                "predicted_label": detection["label"],
                "confidence": detection["confidence"],
                "true_label": "Real"
            })
    
    # Process fake images
    fake_dir = os.path.join(base_dir, "fake")
    if os.path.isdir(fake_dir):
        logger.info(f"Processing fake images from {fake_dir}")
        fake_images = [f for f in os.listdir(fake_dir) 
                      if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
        
        for img_file in tqdm(fake_images, desc="Processing Fake Images"):
            img_path = os.path.join(fake_dir, img_file)
            detection = detect_deepfake(img_path, model)
            
            results.append({
                "filename": img_file,
                "path": img_path,
                "predicted_label": detection["label"],
                "confidence": detection["confidence"],
                "true_label": "Fake"
            })
    
    # Convert to DataFrame
    results_df = pd.DataFrame(results)
    
    if len(results_df) == 0:
        logger.warning("No images were processed. Check directory paths.")
        return
    
    logger.info(f"Processed {len(results_df)} images total")
    
    # Calculate metrics
    metrics = calculate_metrics(results_df)
    
    # Visualize and save results
    visualize_results(results_df, metrics, output_dir)
    
    # Return results for further analysis if needed
    return results_df, metrics

def calculate_metrics(results_df):
    """
    Calculate performance metrics from detection results.
    
    Args:
        results_df: DataFrame with detection results
        
    Returns:
        dict: Dictionary with performance metrics
    """
    # Filter out unknown results
    valid_df = results_df[results_df["predicted_label"] != "Unknown"]
    
    if len(valid_df) == 0:
        logger.warning("No valid predictions for metric calculation")
        return {}
    
    # Calculate confusion matrix
    y_true = valid_df["true_label"].values
    y_pred = valid_df["predicted_label"].values
    
    # Basic metrics
    metrics = {}
    
    try:
        # Confusion matrix
        cm = confusion_matrix(y_true, y_pred, labels=["Real", "Fake"])
        metrics["confusion_matrix"] = cm
        
        # Classification report
        report = classification_report(y_true, y_pred, 
                                      labels=["Real", "Fake"], 
                                      output_dict=True)
        metrics.update(report)
        
        # If we have probability scores and binary labels, calculate ROC
        if all(label in ["Real", "Fake"] for label in valid_df["true_label"].unique()):
            # For ROC curve, we need scores where higher value = more likely to be positive class (Fake)
            y_scores = valid_df["confidence"].values
            y_binary = np.array([1 if label == "Fake" else 0 for label in y_true])
            fpr, tpr, thresholds = roc_curve(y_binary, y_scores)
            metrics["roc"] = {"fpr": fpr, "tpr": tpr, "thresholds": thresholds}
            metrics["auc"] = auc(fpr, tpr)
        
        logger.info(f"Metrics calculated: accuracy={metrics.get('accuracy', 'N/A')}")
    except Exception as e:
        logger.error(f"Error calculating metrics: {str(e)}")
    
    return metrics

def visualize_results(results_df, metrics, output_dir="results"):
    """
    Generate visualizations from detection results.
    
    Args:
        results_df: DataFrame with detection results
        metrics: Dictionary with performance metrics
        output_dir: Directory to save visualizations
    """
    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)
    
    # 1. Plot confidence distribution
    plt.figure(figsize=(10, 6))
    sns.histplot(data=results_df, x="confidence", hue="predicted_label", bins=20)
    plt.title("Confidence Score Distribution")
    plt.xlabel("Confidence Score")
    plt.ylabel("Count")
    plt.savefig(os.path.join(output_dir, "confidence_distribution.png"))
    plt.close()
    
    # 2. Confusion Matrix
    if "confusion_matrix" in metrics:
        plt.figure(figsize=(8, 6))
        sns.heatmap(metrics["confusion_matrix"], annot=True, fmt="d", cmap="Blues",
                   xticklabels=["Real", "Fake"], yticklabels=["Real", "Fake"])
        plt.xlabel("Predicted Label")
        plt.ylabel("True Label")
        plt.title("Confusion Matrix")
        plt.savefig(os.path.join(output_dir, "confusion_matrix.png"))
        plt.close()
    
    # 3. ROC Curve
    if "roc" in metrics:
        plt.figure(figsize=(8, 6))
        plt.plot(metrics["roc"]["fpr"], metrics["roc"]["tpr"], 
                label=f'ROC curve (AUC = {metrics["auc"]:.3f})')
        plt.plot([0, 1], [0, 1], 'k--')
        plt.xlabel('False Positive Rate')
        plt.ylabel('True Positive Rate')
        plt.title('Receiver Operating Characteristic (ROC)')
        plt.legend(loc="lower right")
        plt.savefig(os.path.join(output_dir, "roc_curve.png"))
        plt.close()
    
    # 4. Confidence vs. Correctness
    results_df["correct"] = results_df["predicted_label"] == results_df["true_label"]
    plt.figure(figsize=(10, 6))
    sns.boxplot(data=results_df, x="correct", y="confidence")
    plt.title("Confidence Scores by Prediction Correctness")
    plt.xlabel("Correct Prediction")
    plt.ylabel("Confidence Score")
    plt.savefig(os.path.join(output_dir, "confidence_vs_correctness.png"))
    plt.close()
    
    # 5. Save results to CSV
    results_df.to_csv(os.path.join(output_dir, "detection_results.csv"), index=False)
    
    # 6. Save metrics summary
    with open(os.path.join(output_dir, "metrics_summary.txt"), "w") as f:
        f.write("DeepFake Detection Results Summary\n")
        f.write("==================================\n\n")
        
        f.write(f"Total images processed: {len(results_df)}\n")
        
        # Add counts by category
        real_count = len(results_df[results_df["true_label"] == "Real"])
        fake_count = len(results_df[results_df["true_label"] == "Fake"])
        f.write(f"Real images: {real_count}\n")
        f.write(f"Fake images: {fake_count}\n\n")
        
        if "accuracy" in metrics:
            f.write(f"Accuracy: {metrics['accuracy']:.4f}\n")
        
        if "Fake" in metrics:
            f.write(f"Fake Detection Precision: {metrics['Fake']['precision']:.4f}\n")
            f.write(f"Fake Detection Recall: {metrics['Fake']['recall']:.4f}\n")
            f.write(f"Fake Detection F1-Score: {metrics['Fake']['f1-score']:.4f}\n")
        
        if "Real" in metrics:
            f.write(f"Real Detection Precision: {metrics['Real']['precision']:.4f}\n")
            f.write(f"Real Detection Recall: {metrics['Real']['recall']:.4f}\n")
            f.write(f"Real Detection F1-Score: {metrics['Real']['f1-score']:.4f}\n")
        
        if "auc" in metrics:
            f.write(f"AUC-ROC: {metrics['auc']:.4f}\n")
    
    logger.info(f"Visualizations and results saved to {output_dir}")

# For Jupyter notebook use
if __name__ == "__main__":
    # Example usage:
    # Change these paths to match your environment
    model_path = "xception_deepfake_model.h5"  # Path to your .h5 model file
    test_dir = "test"  # This is your test directory with real/fake subdirectories
    output_dir = "evaluation_results"  # Where to save the results
    
    results_df, metrics = evaluate_model(test_dir, model_path, output_dir)
    
    # Print a summary of the results
    print(f"Accuracy: {metrics.get('accuracy', 'N/A')}")
    if "Fake" in metrics:
        print(f"Fake Detection F1-Score: {metrics['Fake']['f1-score']:.4f}")
    if "Real" in metrics:
        print(f"Real Detection F1-Score: {metrics['Real']['f1-score']:.4f}")

2025-03-31 07:09:41,334 - DeepFakeDetector - INFO - Loading model from xception_deepfake_model.h5
2025-03-31 07:09:42,089 - absl - WARNING - Compiled the loaded model, but the compiled metrics have yet to be built. `model.compile_metrics` will be empty until you train or evaluate the model.
2025-03-31 07:09:42,094 - DeepFakeDetector - INFO - Model loaded successfully
2025-03-31 07:09:42,095 - DeepFakeDetector - INFO - Processing real images from test\real
Processing Real Images:   0%|          | 0/10000 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step


Processing Real Images:   0%|          | 1/10000 [00:01<4:04:42,  1.47s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 158ms/step


Processing Real Images:   0%|          | 2/10000 [00:01<2:03:47,  1.35it/s]

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 69ms/step


Processing Fake Images: 100%|█████████▉| 9767/9768 [24:31<00:00,  9.29it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step


Processing Fake Images: 100%|██████████| 9768/9768 [24:31<00:00,  6.64it/s]
2025-03-31 08:01:13,871 - DeepFakeDetector - INFO - Processed 19768 images total
2025-03-31 08:01:13,972 - DeepFakeDetector - INFO - Metrics calculated: accuracy=0.4844698502630514
2025-03-31 08:01:14,401 - DeepFakeDetector - INFO - Visualizations and results saved to evaluation_results


Accuracy: 0.4844698502630514
Fake Detection F1-Score: 0.4434
Real Detection F1-Score: 0.5199


In [2]:
import tensorflow as tf
from tensorflow.keras.applications import Xception
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D

def create_xception_deepfake_model(model_path='xception_deepfake_model.h5'):
    """
    创建基于Xception的深度伪造检测模型并保存为.h5格式
    
    参数:
        model_path: 保存模型的路径
        
    返回:
        构建好的模型
    """
    # 加载预训练的Xception，不包括顶层分类器
    base_model = Xception(weights='imagenet', include_top=False, input_shape=(299, 299, 3))
    
    # 冻结基础模型层，使其权重在训练期间不更新
    for layer in base_model.layers:
        layer.trainable = False
    
    # 添加自定义分类层
    x = base_model.output
    x = GlobalAveragePooling2D()(x)
    x = Dense(1024, activation='relu')(x)
    predictions = Dense(1, activation='sigmoid')(x)  # 二分类问题：真实/伪造
    
    # 构建完整模型
    model = Model(inputs=base_model.input, outputs=predictions)
    
    # 编译模型
    model.compile(optimizer='adam', 
                  loss='binary_crossentropy', 
                  metrics=['accuracy'])
    
    # 保存模型为.h5格式
    model.save(model_path)
    print(f"Xception模型已创建并保存到{model_path}")
    
    return model

# 执行函数创建模型
model = create_xception_deepfake_model()

2025-03-31 07:09:06,770 - absl - WARNING - You are saving your model as an HDF5 file via `model.save()` or `keras.saving.save_model(model)`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')` or `keras.saving.save_model(model, 'my_model.keras')`. 


Xception模型已创建并保存到xception_deepfake_model.h5
